In [7]:
import numpy as np
import pandas as pd
import geopandas as gpd
from osgeo import gdal
from gdalconst import *
#import osr
import matplotlib.pyplot as plt
%matplotlib qt

#Import bokeh 
import bokeh.plotting as bp
from bokeh.models import ColumnDataSource, Label
from bokeh.layouts import layout
from bokeh.models import HoverTool
from bokeh.palettes import RdYlBu11 as palette
from bokeh.models import LogColorMapper
from bokeh.io import output_notebook
from bokeh.plotting import Figure
import pysal as ps


#Importing raster data. 
from datashader.bokeh_ext import InteractiveImage, HoverLayer
import datashader as ds
import datashader.transfer_functions as tf
import rasterio as rio
from bokeh.plotting.figure import Figure
from skimage.transform import resize
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno



#makes jupyter notebook screen wider
from IPython.core.display import HTML, display
display(HTML("<style>.container { width:80% !important; }</style>"))

In [2]:
#Import the data

#Read a raster
Test_data = "/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/"
Test = gdal.Open(Test_data + "/Mandakini.bil")#Get raster data
M_DEM = Test.ReadAsArray()

#Read stream data
name = "Mandakini_fullProfileMC_forced_0.45_3_1258909000_10_80_281_for_Arc.csv" #Set file name
path = "/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/" #Set path to data
#for csv files
data = np.genfromtxt((path+name), delimiter=',', skip_header=1, names=['id', 'x', 'y', 'chan_number', 'reciever_chan','node_on_reciever_chan', 'node', 'row','column', 'flow_distance', 'chi', 'elevation', 'drainage_area', 'n_data_points', 'm_mean','m_st_dev', 'm_std_err', 'b_mean', 'b_st_dev', 'b_std_err', 'DW_mean', 'DW_st_dev', 'DW_std_err', 'fitted_elev_mean', 'fitted_elev_stdev', 'fitted_elev_std_err'])
#for tree files
#data = np.genfromtxt((path+name), delimiter=' ', skip_header=1, names=['chan_number', 'reciever_chan','node_on_reciever_chan', 'node', 'row','column', 'flow_distance', 'chi', 'elevation', 'drainage_area', 'n_data_points', 'm_mean','m_st_dev', 'm_std_err', 'b_mean', 'b_st_dev', 'b_std_err', 'DW_mean', 'DW_st_dev', 'DW_std_err', 'fitted_elev_mean', 'fitted_elev_stdev', 'fitted_elev_std_err'])

#load csv file as pandas dataframe
df = pd.read_csv(path+name)

##load Raster data
newpath = '/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/'
raster_data = rio.open(newpath+'Mandakini.bil')



# define catagorized dataframe column
#path = '/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/Mandakini_fullProfileMC_forced_0.45_3_1258909000_10_80_281_for_Arc.csv'
#df = pd.read_csv(path, usecols=['x', 'y', 'flow_distance', 'elevation', 'chi'])
df['elevation_cat'] = pd.cut(df['elevation'], bins=[0, 1000, 1500, 2700], labels=['low', 'mid', 'high']).astype('category')




In [34]:
# #Set Ranges
# xmin= 280000
# ymin = 3350000
# xmax = 345000
# ymax = 3410000 #3632767

# x_range = (xmin, xmax)
# y_range = (ymin, ymax)

#to define boundaries of the plot area, default is adding on 1 km to easting and northing
def define_boundaries(df, r=1000):
    xmin = df['x'].min()
    xmax = df['x'].max()
    ymin =df['y'].min()
    ymax = df['y'].max()
    x_range = (xmin-r, xmax+r)
    y_range = (ymin-r, ymax+r)
    return x_range, y_range


In [16]:
#quickref  #For a quick reference of jupyter notebook shortcuts.

In [4]:
#may 9th, using holoviews to plot up raster and points

import holoviews as hv
import geoviews as gv
from cartopy import crs


stream = gv.Dataset(df, kdims=['x', 'y', 'elevation', 'chi'])

streams = stream.to(gv.Points, kdims=['x', 'y'],
                    vdims=['elevation', 'chi'], crs=crs.PlateCarree())

%output backend='bokeh'
%opts Overlay [width=600 height=300 xaxis=None yaxis=None] 
%opts Points (size=0.005 cmap='inferno') [tools=['hover'] color_index=2]

ERROR:root:Line magic function `%output` not found.
ERROR:root:Line magic function `%opts` not found.
ERROR:root:Line magic function `%opts` not found.


In [8]:

def create_base_plot():
    
    # data is in meters
    xmin = 314000 
    ymin = 3368000
    xmax = 332000
    ymax = 3380000
    
    #Define plot canvas area
    cvs = ds.Canvas(plot_width=900,
                    plot_height=600,
                    x_range=(xmin, xmax),
                    y_range=(ymin, ymax))
    
    #
    agg = cvs.points(df, 'x', 'y', ds.mean('elevation'))
    img = tf.shade(agg, cmap=inferno, how='log')
    fig = Figure(x_range=(xmin, xmax),
                 y_range=(ymin, ymax),
                 plot_width=900,
                 plot_height=600,
                 tools='')
    
    fig.background_fill_color = 'black'
    fig.toolbar_location = None
    fig.axis.visible = False
    fig.grid.grid_line_alpha = 0
    fig.min_border_left = 0
    fig.min_border_right = 0
    fig.min_border_top = 0
    fig.min_border_bottom = 0

    fig.image_rgba(image=[img.data],
                   x=[xmin],
                   y=[ymin],
                   dw=[xmax-xmin],
                   dh=[ymax-ymin])
    return fig, (xmin, ymin, xmax, ymax), agg

fig, extent, datashader_agg = create_base_plot()

#

In [9]:
#may 8th , monday, plotting coordinates and datashader rasters
cvs = ds.Canvas(plot_width=900,
                    plot_height=600,
                    x_range=(xmin, xmax),
                    y_range=(ymin, ymax))


#%time tf.shade(cvs.points(df,'x','y'))
glyph = ds.glyphs.Point('x', 'y')

from datashader import reductions
reduction = reductions.count()

from datashader.core import bypixel
agg = bypixel(df, cvs, glyph, reduction)



In [30]:
#Best way to display stream as a datashader image, although this is probably not the way to go.


#tf.shade(cvs.points(df, 'x', 'y', agg=reductions.mean('elevation')))

# cvs = ds.Canvas(plot_width=900, plot_height=900, x_range=(314000,332000),y_range=(3368000,3380000))
# aggr = reductions.mean('elevation')
# img = cvs.points(df, 'x', 'y',agg=aggr)
# tfimg = tf.shade(img, cmap=[(230,230,0), "orangered", "#300030"])
# tf.spread(tfimg)




In [10]:
import bokeh.plotting as bp
from datashader.bokeh_ext import InteractiveImage

bp.output_notebook()

#Bokeh figure, set data source
source=ColumnDataSource(df)


#p = bp.figure(tools='pan,wheel_zoom,reset', x_range=x_range, y_range=y_range)

#p.circle(pdata['x'], pdata['y'], source=source, color='red', size=6)

#setting interactive plot
#my_hover = HoverTool()
#my_hover.tooltips = [('Elevation (m)', '@elevation'), ('Chi (X)', '@chi')]
#p.add_tools(my_hover)



#function to create datashader image
def image_callback(x_range, y_range, w, h):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'x', 'y', ds.reductions.mean('elevation'))
    img = tf.shade(agg)
    return tf.spread(img)#, threshold=0.80)





p = bp.figure(x_range=x_range, y_range=y_range)
p.circle(df['x'][0],df['y'][0], source=source, color='red', size=20)


#interactive image for the raster
#InteractiveImage(p, basic_raster)



#image_callback((314000,332000),(3368000,3380000), 2000, 2000)

#interactive image for the stream
InteractiveImage(p, image_callback)

Loading BokehJS ...

In [19]:
#from bokeh.plotting import figure, output_file, show
#from bokeh.models import HoverTool

bp.output_notebook()

#Set data and data source, ongoing work would be to do this from within the pandas dataframe
x = df['x']
y = df['y']
chi = df['chi']
elevation = df['elevation']
flow_distance = df['flow_distance']
source = ColumnDataSource({'x': x, 'y': y, 'chi': chi, 'elevation': elevation, 'flow_distance': flow_distance})

#using matplot lib colors in bokeh
import matplotlib as mpl

colors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(chi))]


#define tools to use
TOOLS = "pan,wheel_zoom,reset,save,lasso_select"


# Basic plot setup
plot = bp.figure(plot_width=600, plot_height=300,x_range=x_range, y_range=y_range, title='Stream Map')
plot.circle(x, y, size=2, color='gray')
cr = plot.circle(x='x', y='y', size=20,
                fill_color="grey", hover_fill_color="firebrick",
                fill_alpha=0.03, hover_alpha=0.3,
                line_color=None, hover_line_color="white", source=source)
plot.add_tools(HoverTool(tooltips=None, renderers=[cr], mode='mouse'))


plot2 = bp.figure(plot_width=500, plot_height=250, toolbar_location='above', 
               title='Elevation profile', x_axis_label='Flow Distance (m)', y_axis_label='Elevation (m)')
plot2.circle(flow_distance, elevation, size=2, color=colors)
cr2 = plot2.circle(x='flow_distance', y='elevation', size=20,
                 fill_color='grey', hover_fill_color="firebrick",
                 fill_alpha=0.03, hover_alpha=0.3,
                 line_color=None, hover_line_color="white", source=source)
plot2.add_tools(HoverTool(tooltips=None, renderers=[cr2], mode='mouse'))

plot3 = bp.figure(plot_width=500, plot_height=250, toolbar_location='above', 
               title='Chi profile', x_axis_label='Chi (X)', y_axis_label='Elevation (m)')
plot3.circle(chi, elevation, size=2, color=colors)
cr3 = plot3.circle(x='chi', y='elevation', size=20,
                 fill_color='grey', hover_fill_color="firebrick",
                 fill_alpha=0.03, hover_alpha=0.3,
                 line_color=None, hover_line_color="white", source=source)
plot3.add_tools(HoverTool(tooltips=None, renderers=[cr3], mode='mouse'))




out = layout([[plot],[plot2], [plot3]])



bp.show(out)


Loading BokehJS ...

In [66]:
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno

import holoviews as hv
import geoviews as gv
from cartopy import crs

background = "black"

export = partial(export_image, background = background, export_path="export")
cm = partial(colormap_select, reverse=(background!="black"))

source = ColumnDataSource(df)

#Define boundaries
x_range, y_range = define_boundaries(df, 10000)


f = Figure(x_range=x_range, y_range=y_range)
f.circle(df['x'],df['y'], source=source, color='red', size=10)



def base_plot(tools='pan,wheel_zoom,reset',plot_width=600, plot_height=600, x_range=None, y_range=None, **plot_args):
    p = Figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
              x_range=x_range, y_range=y_range, outline_line_color=None,
              min_border=0, min_border_left=0, min_border_right=0,
              min_border_top=0, min_border_bottom=0, **plot_args)
    #sizing_mode='scale_both',
    p.axis.visible = True
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    #p.add_title(STAMEN_TONER, alpha=0.5)
    return p



def basic_raster(x_range, y_range, w, h, how='log'):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.raster(raster_data)
    return tf.shade(agg, cmap=cm(inferno), how='linear', alpha=200) #tf.interpolate(...cmap=['darkred', 'white', 'darkblue'])



p = base_plot(x_range=x_range, y_range=y_range)
p.circle(df['x'],df['y'], source=source, color='red', size=10)

ii = InteractiveImage(plot, basic_raster)

# p = figure(title="Stream channel elevation map")
# p.circle(df['x'], df['y'], source=source, color='red', size=6)

#ii #* hv.Points([(df['x'][0],df['y'][0])])

InteractiveImage(p, basic_raster)

# out = layout([[ii]])#,[plot2], [plot3]])



# show(out)


/Users/bmelosh/anaconda2/envs/geospatial/lib/python2.7/site-packages/bokeh/util/deprecation.py:34: BokehDeprecationWarning: 
Supplying a user-defined data source AND iterable values to glyph methods is deprecated.

See https://github.com/bokeh/bokeh/issues/2056 for more information.

  warn(message)
/Users/bmelosh/anaconda2/envs/geospatial/lib/python2.7/site-packages/bokeh/util/deprecation.py:34: BokehDeprecationWarning: 
Supplying a user-defined data source AND iterable values to glyph methods is deprecated.

See https://github.com/bokeh/bokeh/issues/2056 for more information.

  warn(message)
/Users/bmelosh/anaconda2/envs/geospatial/lib/python2.7/site-packages/bokeh/util/deprecation.py:34: BokehDeprecationWarning: 
Supplying a user-defined data source AND iterable values to glyph methods is deprecated.

See https://github.com/bokeh/bokeh/issues/2056 for more information.

  warn(message)
/Users/bmelosh/anaconda2/envs/geospatial/lib/python2.7/site-packages/bokeh/util/deprecation.py:34

In [47]:
w

NameError: name 'w' is not defined

In [13]:
#May 9th, working with streamlining datashader image and bokeh interactive plot with holoviews
import pandas as pd
import holoviews as hv
import geoviews as gv
import datashader as ds
import dask.dataframe as dd

from bokeh.models import WMTSTileSource
from cartopy import crs
from matplotlib.cm import get_cmap
from holoviews.operation.datashader import datashade, aggregate

from dask.diagnostics import ProgressBar
from dask.cache import Cache
ProgressBar().register()
Cachey(9e9).register()

hv.notebook_extension('bokeh', width=900)

%opts Overlay [width=800 height=455 xaxis=None yaxis=None show_grid=False] 
%opts Shape (fill_color=None line_width=1.5) [apply_ranges=False] 
%opts Points [apply_ranges=False] WMTS (alpha=0.5) NdOverlay [tools=['tap']]


# output_notebook()


NameError: name 'Cachey' is not defined